In [3]:
import torch
import torch.nn as nn
import coremltools as ct

In [4]:
from model import LPIENet
model = LPIENet(3, 3, [16, 32, 64], [32, 16])

In [5]:
model.load_state_dict(torch.load('PIEFSRA/Saves/Model_Saves/best.pth'))
model.eval()

LPIENet(
  (_encoders): ModuleList(
    (0): Sequential(
      (0): Conv2d(3, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): BaseBlock(
        (_conv0): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_dw_conv): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), groups=16)
        (_conv1): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_conv2): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_conv3): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
      )
      (2): BaseBlock(
        (_conv0): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_dw_conv): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), groups=16)
        (_conv1): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_conv2): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
        (_conv3): Conv2d(16, 16, kernel_size=(1, 1), stride=(1, 1))
      )
      (3): AttentionBlock(
        (_spatial_attention_conv): Conv2d(

In [6]:
example_input = torch.randn(1,3,540,960)
traced_model = torch.jit.trace(model, example_input)
out = model(example_input)

In [7]:
import torch
print(torch.__version__)

2.0.1+cu117


In [37]:
import coremltools as ct
import torch

# PyTorch 모델을 로드하고 예시 입력을 만듭니다.
# (이 예시에서는 임의의 traced_model과 example_input 사용)
# 예시:
# traced_model = torch.jit.trace(pytorch_model, example_input)
# example_input = torch.randn(1, 3, 540, 960)

# 모델 변환
model = ct.convert(
    traced_model,
    inputs=[ct.ImageType(shape=example_input.shape, bias=[-1,-1,-1], scale=2.0/255.0)],
    minimum_deployment_target=ct.target.iOS14  # 또는 ct.target.macOS11
)

# 모델 저장
model.save("letgo.mlmodel")


Translating MIL ==> NeuralNetwork Ops: 100%|██████████| 747/747 [00:00<00:00, 28508.54 ops/s]


In [46]:
# save model
from coremltools.proto import FeatureTypes_pb2 as ft
from coremltools.models.utils import save_spec

spec = model.get_spec()
print(spec)
builder = ct.models.neural_network.NeuralNetworkBuilder(spec=spec)
builder.add_squeeze(name="squeeze", input_name="var_892", output_name="squeeze_out", axes =None, squeeze_all= True)
builder.add_activation(name="activation", non_linearity="LINEAR", input_name="squeeze_out", output_name="activation_out", params=[127.5, 127.5])

builder.spec.description.output.pop()
builder.spec.description.output.add()
output = builder.spec.description.output[0]
output.name = "activation_out"

output.type.imageType.colorSpace = ft.ImageFeatureType.ColorSpace.Value("RGB")
output.type.imageType.width = 960 
output.type.imageType.height = 540

save_spec(builder.spec, "letgo.mlmodel")

specificationVersion: 5
description {
  input {
    name: "x_1"
    type {
      imageType {
        width: 960
        height: 540
        colorSpace: RGB
      }
    }
  }
  output {
    name: "var_892"
    type {
      multiArrayType {
        dataType: FLOAT32
      }
    }
  }
  metadata {
    userDefined {
      key: "com.github.apple.coremltools.source"
      value: "torch==2.0.1+cu117"
    }
    userDefined {
      key: "com.github.apple.coremltools.source_dialect"
      value: "TorchScript"
    }
    userDefined {
      key: "com.github.apple.coremltools.version"
      value: "7.2"
    }
  }
}
neuralNetwork {
  layers {
    name: "input.1"
    input: "x_1"
    output: "input.1"
    convolution {
      outputChannels: 16
      kernelChannels: 3
      nGroups: 1
      kernelSize: 3
      kernelSize: 3
      stride: 1
      stride: 1
      dilationFactor: 1
      dilationFactor: 1
      valid {
        paddingAmounts {
          borderAmounts {
            startEdgeSize: 1
      

In [ ]:

model.save("newmodel_BGR.mlpackage")